<h3>Assignment 7 (Midsem)</h3>

In [316]:
import pandas as pd
import numpy as np
import plotly.express as px
from scipy.stats import kurtosis,skew
import statsmodels.api as sm
import matplotlib.pyplot as plt
# pd.set_option('display.max_rows', None)  # Show all rows
# pd.set_option('display.max_columns', None)  # Show all columns

In [317]:
df = pd.read_csv("e7-htr-currernt.csv")

In [318]:
current = list(df["HT R Phase Current"])
timestamp = list(df["Timestamp"])
days = []
for i in timestamp:
    k = i[:2]
    days.append(k)

In [319]:
df['Time'] = pd.to_datetime(df['Timestamp'], format='%d-%m-%Y %H:%M').dt.time
df['Day'] = pd.to_datetime(df['Timestamp'], format='%d-%m-%Y %H:%M').dt.day

In [320]:
day_hash = np.zeros(len(days))
day_hash[0] = int(1)
current_date = days[0]
index = int(1)
for k in range(0, len(days)):
    temp = days[k]
    if temp != current_date:
        index += int(1)
        current_date = temp
        day_hash[k] += int(index)
    else:
        day_hash[k] = int(index)

df["Day No."] = day_hash
df

Timestamp  HT R Phase Current      Time  Day  Day No.
0      23-12-2018 05:30                 0.0  05:30:00   23      1.0
1      23-12-2018 05:35                 0.0  05:35:00   23      1.0
2      23-12-2018 05:40                 0.0  05:40:00   23      1.0
3      23-12-2018 05:45                 0.0  05:45:00   23      1.0
4      23-12-2018 05:50                 0.0  05:50:00   23      1.0
...                 ...                 ...       ...  ...      ...
81721  04-10-2019 23:35                 0.0  23:35:00    4    285.0
81722  04-10-2019 23:40                 0.0  23:40:00    4    285.0
81723  04-10-2019 23:45                 0.0  23:45:00    4    285.0
81724  04-10-2019 23:50                 0.0  23:50:00    4    285.0
81725  04-10-2019 23:55                 0.0  23:55:00    4    285.0

[81726 rows x 5 columns]

In [321]:
overall_avg = np.mean(df["HT R Phase Current"])
# print(overall_avg)
Mean, Error, Std_dev, Sum, Precentage_obeserved = [], [], [], [], []
Daily_readings = []
for i in range(1, 286):
    unfiltered_readings = df["HT R Phase Current"][df['Day No.'] == i]
    readings = df[df['Day No.'] == i][df["HT R Phase Current"]>0.2]
    readings
    # Daily_readings.append(readings)
    sum = np.sum(readings['HT R Phase Current'])
    Sum.append(sum)
    mean = np.mean(readings['HT R Phase Current'])
    Mean.append(mean)
    # error = overall_avg - mean
    # Error.append(error)
    std_dev = np.std(readings['HT R Phase Current'])
    Std_dev.append(std_dev)
    Precentage_obeserved.append(len(readings)/len(unfiltered_readings)*100)
    # median = np.median(readings)
    # Median.append(median)
    # print(f"Day {i}: Overall Mean = {overall_avg}, Mean = {mean}, Median = {median}, Error = {error}, Standard Deviation = {std_dev}.")

/tmp/ipykernel_9689/2457107976.py:7: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.

/tmp/ipykernel_9689/2457107976.py:7: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.

/tmp/ipykernel_9689/2457107976.py:7: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.

/tmp/ipykernel_9689/2457107976.py:7: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.

/tmp/ipykernel_9689/2457107976.py:7: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.

/tmp/ipykernel_9689/2457107976.py:7: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.

/tmp/ipykernel_9689/2457107976.py:7: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.

/tmp/ipykernel_9689/2457107976.py:7: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.

/tmp/ipykernel_9689/2457107976.py:7: UserWarning:

Boolean Series key will be re

In [322]:
Days = np.arange(1,day_hash[len(day_hash) - 1] + 1)
labels = ['Day', 'Sum', 'Mean', 'Standard Deviation', 'Percentage Observed']
data = {'Day':Days, 'Sum': Sum, 'Mean': Mean, 'Standard Deviation': Std_dev, 'Percentage Observed': Precentage_obeserved}
Daily_data = pd.DataFrame(data)
# Daily_data.sort_values(by='Mean')
Daily_data

Day      Sum       Mean  Standard Deviation  Percentage Observed
0      1.0  4050.84  38.215472           23.540627            47.747748
1      2.0  3065.04  32.606809           21.517334            32.638889
2      3.0  6177.84  45.093723           23.384410            47.569444
3      4.0  5011.53  37.680677           22.335360            46.180556
4      5.0  4400.42  32.838955           23.263639            46.527778
..     ...      ...        ...                 ...                  ...
280  281.0   143.91   6.256957            4.752774             7.986111
281  282.0  4980.59  34.113630           30.235446            50.694444
282  283.0  6366.10  43.904138           31.514284            50.347222
283  284.0  5869.32  41.626383           30.542434            48.958333
284  285.0     0.00        NaN                 NaN             0.000000

[285 rows x 5 columns]

In [323]:
px.line(df,x=df['Timestamp'], y=['HT R Phase Current'], animation_frame=df['Day No.']).update_yaxes(range=[0,100])

In [324]:
# def data_points_in_range(day, tolerance):
#     upper_lim = Mean[day-1]+tolerance*Std_dev[day-1]
#     lower_lim = Mean[day-1]-tolerance*Std_dev[day-1]
#     req_data1 = df[df['HT R Phase Current']>0.1][df['Day No.']==day]
#     normal_data = (req_data1[(df['HT R Phase Current']>lower_lim) & (df['HT R Phase Current']<upper_lim)])
#     if len(req_data1) == 0:
#         return 0
#     else:
#         return len(normal_data)/len(req_data1)

# normal_points_count = [data_points_in_range(day, tolerance=0.8)*100 for day in range(1, int(day_hash[len(day_hash) - 1]) + 1)]
# Daily_data['Normal points (%)'] = normal_points_count

# def unwanted_points(day, threshold=1):
#     req_data2 = df['HT R Phase Current'][df['Day No.'] == day]
#     readings_less_than_threshold = (req_data2 < threshold).sum()  
#     return (readings_less_than_threshold / len(req_data2)) * 100 

# unwanted = [unwanted_points(day) for day in range(1, int(day_hash[len(day_hash) - 1]) + 1)]
# Daily_data['Unwanted (%)'] = unwanted

def std_dev_bandwidth(day, threshold):
    req_data = df['HT R Phase Current'][df['HT R Phase Current'] >= threshold][df['Day No.']==day]
    Std_dev_band = np.std(req_data)
    return Std_dev_band
std_dev_band_data = [std_dev_bandwidth(day, threshold=60) for day in range(1, int(day_hash[len(day_hash) - 1]) + 1)]
Daily_data['Band Standard Deviation'] = std_dev_band_data
def std_dev_sidebandwidth(day, threshold_l, threshold_h):
    req_data = df['HT R Phase Current'][(df['HT R Phase Current'] >= threshold_l) & (df['HT R Phase Current'] <= threshold_h)][df['Day No.']==day]
    Std_dev_band = np.std(req_data)
    return Std_dev_band
std_dev_sideband_data = [std_dev_sidebandwidth(day, threshold_l=20, threshold_h=80) for day in range(1, int(day_hash[len(day_hash) - 1]) + 1)]
Daily_data['SideBand Standard Deviation'] = std_dev_sideband_data

Daily_data

Day      Sum       Mean  Standard Deviation  Percentage Observed  \
0      1.0  4050.84  38.215472           23.540627            47.747748   
1      2.0  3065.04  32.606809           21.517334            32.638889   
2      3.0  6177.84  45.093723           23.384410            47.569444   
3      4.0  5011.53  37.680677           22.335360            46.180556   
4      5.0  4400.42  32.838955           23.263639            46.527778   
..     ...      ...        ...                 ...                  ...   
280  281.0   143.91   6.256957            4.752774             7.986111   
281  282.0  4980.59  34.113630           30.235446            50.694444   
282  283.0  6366.10  43.904138           31.514284            50.347222   
283  284.0  5869.32  41.626383           30.542434            48.958333   
284  285.0     0.00        NaN                 NaN             0.000000   

     Band Standard Deviation  SideBand Standard Deviation  
0                   2.155259                    12.713283  
1                   1.770236                    15.162358  
2                   2.275055                    12.073110  
3                   0.746403                    11.325398  
4                   1.026450                    12.587725  
..                       ...                          ...  
280                      NaN                          NaN  
281                 6.768857                    22.233072  
282                 5.647288                    20.124645  
283                 5.908420                    18.601604  
284                      NaN                          NaN  

[285 rows x 7 columns]

In [325]:
# # Good_days = Daily_data['Day'][Daily_data['Mean']>30][(Daily_data['Standard Deviation']<37)][(Daily_data['Band Standard Deviation']<6) | ((Daily_data['SideBand Standard Deviation']<9) & (Daily_data['SideBand Standard Deviation']>1))]
Missing_days = Daily_data['Day'][Daily_data['Percentage Observed'] < 26.23958]
missing_day_disp = np.array(Missing_days)
print(missing_day_disp)
print(f"Number of missing days are {len(Missing_days)}.")
day_classification = np.zeros(285, dtype="str")
for i in Missing_days:
    day_classification[int(i) - 1] = 'M'
print(day_classification)

Good_Bad_Daily = Daily_data[~Daily_data['Day'].isin(Missing_days)]

[ 11.  12.  13.  14.  16.  17.  18.  19.  20.  21.  22.  23.  24.  25.
  26.  27.  28.  29.  30.  31.  33.  46.  59.  60.  61.  62.  63.  64.
  65.  66.  67.  68.  69.  70.  76.  78.  81.  82.  83.  92.  93.  98.
 178. 183. 184. 185. 209. 210. 232. 244. 245. 246. 247. 276. 277. 281.
 285.]
Number of missing days are 57.
['' '' '' '' '' '' '' '' '' '' 'M' 'M' 'M' 'M' '' 'M' 'M' 'M' 'M' 'M' 'M'
 'M' 'M' 'M' 'M' 'M' 'M' 'M' 'M' 'M' 'M' '' 'M' '' '' '' '' '' '' '' '' ''
 '' '' '' 'M' '' '' '' '' '' '' '' '' '' '' '' '' 'M' 'M' 'M' 'M' 'M' 'M'
 'M' 'M' 'M' 'M' 'M' 'M' '' '' '' '' '' 'M' '' 'M' '' '' 'M' 'M' 'M' '' ''
 '' '' '' '' '' '' 'M' 'M' '' '' '' '' 'M' '' '' '' '' '' '' '' '' '' ''
 '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' ''
 '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' ''
 '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' 'M' '' ''
 '' '' 'M' 'M' 'M' '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' '' ''
 '' '' '' '' '

In [326]:
Missing_days_data = df[df['Day No.'].isin(Missing_days)]
Missing_days_data
Missing_days_daily_data = Daily_data[Daily_data['Day'].isin(Missing_days)]
Missing_days_daily_data.to_csv('Missing_Daily_data.csv')

In [327]:
px.line(Missing_days_data,x=Missing_days_data['Timestamp'], y=['HT R Phase Current'], animation_frame=Missing_days_data['Day No.']).update_yaxes(range=[0,100])

In [328]:
Daily_data.to_csv('Daily_data.csv')

In [329]:
# Good_days = Daily_data['Day'][Daily_data['Mean']>30][(Daily_data['Standard Deviation']<37)][(Daily_data['Band Standard Deviation']<6) | ((Daily_data['SideBand Standard Deviation']<9) & (Daily_data['SideBand Standard Deviation']>1))]
Good_days = Good_Bad_Daily['Day'][Daily_data['Sum'] > 3600][Daily_data['Standard Deviation'] < 32]
good_day_disp = np.array(Good_days)
print(good_day_disp)
print(f"Number of good days are {len(Good_days)}.")
for i in Good_days:
    day_classification[int(i) - 1] = 'G'
print(day_classification)

[  1.   3.   4.   5.   6.   7.   8.   9.  10.  15.  32.  37.  38.  39.
  40.  41.  42.  43.  44.  45.  48.  49.  50.  51.  52.  53.  54.  55.
  56.  57.  58.  71.  72.  73.  74.  75.  77.  79.  80.  84.  85.  86.
  87.  88.  89.  90.  91.  94.  95.  96.  97.  99. 100. 101. 102. 103.
 104. 105. 106. 108. 109. 110. 111. 112. 113. 114. 116. 119. 120. 121.
 122. 123. 124. 125. 126. 127. 128. 129. 130. 131. 132. 133. 134. 135.
 136. 137. 138. 139. 140. 141. 142. 144. 145. 146. 147. 148. 149. 150.
 151. 152. 153. 154. 155. 156. 157. 158. 159. 160. 161. 162. 163. 164.
 165. 166. 167. 168. 169. 170. 171. 174. 175. 177. 182. 186. 187. 192.
 193. 195. 196. 197. 198. 199. 200. 201. 203. 205. 207. 211. 212. 213.
 214. 219. 220. 221. 224. 225. 228. 229. 230. 231. 233. 234. 235. 236.
 237. 238. 240. 243. 248. 251. 253. 256. 260. 261. 262. 263. 264. 265.
 266. 267. 268. 270. 271. 272. 273. 274. 275. 278. 279. 280. 282. 283.
 284.]
Number of good days are 183.
['G' '' 'G' 'G' 'G' 'G' 'G' 'G' 'G' 'G' '

Good Days Dataframe


In [330]:
Good_days_data = df[df['Day No.'].isin(Good_days)]
Good_days_data
Good_days_daily_data = Daily_data[Daily_data['Day'].isin(Good_days)]
Good_days_daily_data.to_csv('Good_Daily_data.csv')

In [331]:
px.line(Good_days_data,x=Good_days_data['Timestamp'], y=['HT R Phase Current'], animation_frame=Good_days_data['Day No.']).update_yaxes(range=[0,100])

Smoothening

In [332]:
# data = Good_days_data[Good_days_data['Day No.'].isin(Good_days)]
# Smoothened_data = data['HT R Phase Current'].ewm(span=3, adjust=False).mean()
# Good_days_data['Smoothened Current Values'] = Smoothened_data
# Good_days_data

In [333]:
# px.line(Good_days_data,x=Good_days_data['Timestamp'], y=['Smoothened Current Values'], animation_frame=Good_days_data['Day No.']).update_yaxes(range=[0,100])

In [334]:
import random
training_days = Good_days_data['Day No.'].sample(n=int(0.8*len(Good_days_data)), random_state=random.randint(0,284))
testing_days = Good_days_data['Day No.'].drop(index=training_days.index)
training_days

30847    109.0
29886    106.0
68045    238.0
40161    141.0
24554     87.0
         ...  
45517    160.0
20679     74.0
59133    207.0
38060    134.0
37407    132.0
Name: Day No., Length: 42110, dtype: float64

In [335]:
Training_data = Good_days_data[Good_days_data['Day No.'].isin(training_days)]
Training_data['Time'] = Training_data['Time'].apply(lambda x: x.hour + x.minute/60)
Training_data['Time2'] = Training_data['Time']**2
Training_data['Time3'] = Training_data['Time']**3
Training_data['Time4'] = Training_data['Time']**4
Training_data['Time5'] = Training_data['Time']**5
Training_data['Time6'] = Training_data['Time']**6
Training_data['Time7'] = Training_data['Time']**7
Training_data['Day2'] = Training_data['Day']**2
Training_data

Timestamp  HT R Phase Current       Time  Day  Day No.  \
0      23-12-2018 05:30                 0.0   5.500000   23      1.0   
1      23-12-2018 05:35                 0.0   5.583333   23      1.0   
2      23-12-2018 05:40                 0.0   5.666667   23      1.0   
3      23-12-2018 05:45                 0.0   5.750000   23      1.0   
4      23-12-2018 05:50                 0.0   5.833333   23      1.0   
...                 ...                 ...        ...  ...      ...   
81433  03-10-2019 23:35                 0.1  23.583333    3    284.0   
81434  03-10-2019 23:40                 0.1  23.666667    3    284.0   
81435  03-10-2019 23:45                 0.1  23.750000    3    284.0   
81436  03-10-2019 23:50                 0.0  23.833333    3    284.0   
81437  03-10-2019 23:55                 0.0  23.916667    3    284.0   

            Time2         Time3          Time4         Time5         Time6  \
0       30.250000    166.375000     915.062500  5.032844e+03  2.768064e+04   
1       31.173611    174.052662     971.794030  5.425850e+03  3.029433e+04   
2       32.111111    181.962963    1031.123457  5.843033e+03  3.311052e+04   
3       33.062500    190.109375    1093.128906  6.285491e+03  3.614157e+04   
4       34.027778    198.495370    1157.889660  6.754356e+03  3.940041e+04   
...           ...           ...            ...           ...           ...   
81433  556.173611  13116.427662  309329.085696  7.295011e+06  1.720407e+08   
81434  560.111111  13255.962963  313724.456790  7.424812e+06  1.757206e+08   
81435  564.062500  13396.484375  318166.503906  7.556454e+06  1.794658e+08   
81436  568.027778  13537.995370  322655.556327  7.689957e+06  1.832773e+08   
81437  572.006944  13680.499421  327191.944493  7.825341e+06  1.871561e+08   

              Time7  Day2  
0      1.522435e+05   529  
1      1.691433e+05   529  
2      1.876263e+05   529  
3      2.078141e+05   529  
4      2.298357e+05   529  
...             ...   ...  
81433  4.057293e+09     9  
81434  4.158720e+09     9  
81435  4.262313e+09     9  
81436  4.368109e+09     9  
81437  4.476149e+09     9  

[52638 rows x 12 columns]

In [336]:
import statsmodels.api as sm
#filtered_df['Time'] = pd.to_datetime(filtered_df['Time'])
drop_columns = ['Timestamp', 'HT R Phase Current', 'Date', 'Day Index', 'EMA Current']
X_train = Training_data.drop(columns=drop_columns)
X_train = sm.add_constant(X_train)
y_train = Training_data['EMA Current']
model = sm.OLS(y_train, X_train).fit()
print(model.summary())

KeyError: "['Date', 'Day Index', 'EMA Current'] not found in axis"

In [ ]:
testing_df = filtered_df[filtered_df['Day Index'].isin(testing_days)]
testing_df['Time'] = testing_df['Time'].apply(lambda x: x.hour + x.minute/60)
testing_df['Time2'] = testing_df['Time']**2
testing_df['Time3'] = testing_df['Time']**3
testing_df['Time4'] = testing_df['Time']**4
testing_df['Time5'] = testing_df['Time']**5
testing_df['Time6'] = testing_df['Time']**6
testing_df['Time7'] = testing_df['Time']**7
testing_df['Day2'] = testing_df['Day']**2
testing_df

NameError: name 'filtered_df' is not defined

In [ ]:
drop_columns = ['Timestamp', 'HT R Phase Current', 'Date', 'Day Index', 'EMA Current']
X_test = Training_data.drop(columns=drop_columns)
X_test = sm.add_constant(X_test)
y_test = Training_data['EMA Current']
y_pred_test = model.predict(X_test)

In [ ]:
X_test

In [ ]:
import sklearn.metrics as metrics
y = training_df['HT R Phase Current']
print(metrics.r2_score(y, y_pred_test))
print(metrics.r2_score(y_test, y_pred_test))

In [ ]:
testing_df['Pred Current'] = np.array(y_pred_test[-len(testing_df):]).reshape(-1, 1)
px.line(testing_df, x='Timestamp', y=['HT R Phase Current', 'Pred Current'], animation_frame='Day Index').update_yaxes(range=[0,100])

In [ ]:
df['Time'] = pd.to_datetime(df['Time'], format='%H:%M:%S').dt.time
df['Time'] = df['Time'].apply(lambda x: x.hour + x.minute/60)
df

In [ ]:
df['Time2'] = df['Time']**2
df['Time3'] = df['Time']**3
df['Time4'] = df['Time']**4
df['Time5'] = df['Time']**5
df['Time6'] = df['Time']**6
df['Time7'] = df['Time']**7
df['Day2'] = df['Day']**2
df

In [ ]:
drop_columns = ['Timestamp', 'HT R Phase Current', 'Date', 'Day Index']
X_data = df.drop(columns=drop_columns)
X_data = sm.add_constant(X_data)
y_data = df['HT R Phase Current']
y_pred = model.predict(X_data)
print(metrics.r2_score(y_data, y_pred))
df['Pred Current'] = y_pred

In [ ]:
px.line(df, x='Timestamp', y=['HT R Phase Current', 'Pred Current'], animation_frame='Day Index')